In [1]:
import gym
from gym import spaces
import numpy as np
import torch
from sklearn.metrics import r2_score
from scipy import stats

import xgboost as xgb
import numpy as np
from sklearn.datasets import make_regression
from sklearn.model_selection import train_test_split
import gym
from gym import spaces
import torch
import numpy as np
from scipy import stats


from stable_baselines3.common.vec_env import DummyVecEnv


from sb3_contrib import ARS # 機率輸出不會改變
from stable_baselines3 import A2C # 機率輸出會改變
from stable_baselines3 import DDPG # 輸出機率和動作長依樣?
from stable_baselines3 import HER # 這要搭配其他使用
from stable_baselines3 import PPO # 機率輸出會改變
from stable_baselines3 import SAC # 機率輸出會改變
from stable_baselines3 import TD3 # 輸出機率和動作長依樣?
from sb3_contrib import TRPO
from sb3_contrib import TQC
from sb3_contrib import RecurrentPPO # MlpLstmPolicy

In [2]:
# Generate synthetic data
n_samples = 5000
n_features = 53
n_informative = 53
n_targets = 27
noise = 0.1
random_seed = np.random.randint(0, 1000)

X, y = make_regression(n_samples=n_samples, n_features=n_features, n_informative=n_informative, n_targets=n_targets, noise=noise, random_state=random_seed)

reg = xgb.XGBRegressor(n_estimators=100,multi_strategy="multi_output_tree")
X_train, X_test, y_train, y_test = train_test_split(X, y, test_size=0.33, random_state=random_seed)
reg.fit(X_train, y_train)


XGBRegressor(base_score=None, booster=None, callbacks=None,
             colsample_bylevel=None, colsample_bynode=None,
             colsample_bytree=None, device=None, early_stopping_rounds=None,
             enable_categorical=False, eval_metric=None, feature_types=None,
             gamma=None, grow_policy=None, importance_type=None,
             interaction_constraints=None, learning_rate=None, max_bin=None,
             max_cat_threshold=None, max_cat_to_onehot=None,
             max_delta_step=None, max_depth=None, max_leaves=None,
             min_child_weight=None, missing=nan, monotone_constraints=None,
             multi_strategy='multi_output_tree', n_estimators=100, n_jobs=None,
             num_parallel_tree=None, random_state=None, ...)

In [3]:
y_pred = reg.predict(X_test)
from sklearn.metrics import r2_score
r2_score(y_test, y_pred,multioutput='raw_values')

array([0.58916154, 0.60631216, 0.60750876, 0.59969102, 0.59530746,
       0.61976397, 0.62125429, 0.59766217, 0.61479773, 0.61255206,
       0.59598303, 0.61823986, 0.58374643, 0.60605194, 0.62380498,
       0.61495456, 0.60850801, 0.59264573, 0.60305445, 0.61510826,
       0.61688968, 0.60633583, 0.59480492, 0.60428475, 0.61988806,
       0.59042486, 0.60695809])

In [8]:
import gym
from gym import spaces
import numpy as np
import torch
from sklearn.metrics import r2_score
from scipy import stats

class CustomEnv(gym.Env):
    def __init__(self, S, A, model, max_step=100, device='cpu'):
        self.device = device
        
        # Normalize S and A
        self.S = torch.tensor(S, dtype=torch.float32)#self._normalize(torch.tensor(S, dtype=torch.float32)).to(self.device)
        self.A = torch.tensor(A, dtype=torch.float32)#self._normalize(torch.tensor(A, dtype=torch.float32)).to(self.device)
        
        self.num_samples = self.S.shape[0]
        self.current_step = 0
        self.model = model
        self.max_step = max_step
        self.action_instance = self.A.shape[0]
        self.action_dim = self.A.shape[1]
        
        # 计算边界（假设数据大致遵循正态分布）
        self.obs_low = float(self.S.min())*1.5
        self.obs_high = float(self.S.max())*1.5
        self.action_low = float(self.A.min())*1.5
        self.action_high = float(self.A.max())*1.5

        # Limit the action space
        self.action_space = spaces.Box(low=self.action_low, high=self.action_high, shape=(self.action_instance, self.action_dim), dtype=np.float32)
        
        self.obs_dim_S = self.S.shape[1]
        self.observation_space = spaces.Box(low=self.obs_low, high=self.obs_high, shape=(self.num_samples, self.obs_dim_S), dtype=np.float32)
        
    # def _normalize(self, tensor):
    #     mean = tensor.mean(dim=0, keepdim=True)
    #     std = tensor.std(dim=0, keepdim=True)
    #     return (tensor - mean) / (std + 1e-8)  # Add small epsilon to avoid division by zero
    
    # def _denormalize(self, tensor, original):
    #     mean = original.mean(dim=0, keepdim=True)
    #     std = original.std(dim=0, keepdim=True)
    #     return tensor * (std + 1e-8) + mean

    def reset(self):
        self.current_step = 0
        return self.S.cpu().numpy()
    
    def step(self, action):
        # 确保动作在边界内
        #action = np.clip(action, -1, 1)
        action = torch.tensor(action, dtype=torch.float32).to(self.device)
        
        # 在使用之前反标准化动作
        denorm_action = action#self._denormalize(action, self.A)
        
        reward, score = self._calculate_reward(denorm_action)
        #print("STEP.....","reward: ",reward,"score: ",score)
        best_action = None
        best_score = float('-inf')
        if reward > 0 and score is not None:
            # 如果 score 是张量，取其平均值
            current_score = score.mean().item() if isinstance(score, torch.Tensor) else score
            if current_score > best_score:
                best_score = current_score
                best_action = denorm_action.cpu().numpy()  # 将最佳动作转换为 numpy 数组

        done = (self.current_step == self.max_step - 1)
        self.current_step += 1
        
        return self.S.cpu().numpy(), reward, done, {"best_action": best_action, "best_score": best_score}
    
    def _calculate_reward(self, action):
        try:
            y_pred_observe = torch.tensor(self.model.predict(action.cpu().numpy()), dtype=torch.float32).to(self.device)
            y_pred = torch.tensor(self.model.predict(self.A.cpu().numpy()), dtype=torch.float32).to(self.device)

            # 反标准化预测和真实值以进行正确的 R2 计算
            # denorm_S = self._denormalize(self.S, self.S)
            # denorm_y_pred_observe = self._denormalize(y_pred_observe, self.S)
            # denorm_y_pred = self._denormalize(y_pred, self.S)

            r2_observe = r2_score(self.S.cpu().numpy(), y_pred_observe.cpu().numpy(), multioutput='raw_values')
            r2_ground = r2_score(self.S.cpu().numpy(), y_pred.cpu().numpy(), multioutput='raw_values')

            # 检查 NaN 值
            if np.isnan(r2_observe).any() or np.isnan(r2_ground).any():
                return 0.0, None

            score = None
            #print("r2_observe: ",r2_observe,"r2_ground: ",r2_ground)
            if stats.ttest_ind(r2_observe, r2_ground, alternative="greater").pvalue < 0.05:
                reward = float(np.mean(r2_observe) - np.mean(r2_ground))  # 连续奖励
                score = r2_observe
                
            elif stats.ttest_ind(r2_observe, r2_ground, alternative="less").pvalue < 0.05:
                reward = float(np.mean(r2_observe) - np.mean(r2_ground))  # 负奖励
            else:
                reward = 0.0
            
            return reward, torch.tensor(score).to(self.device) if score is not None else None
        
        except Exception as e:
            print(f"Error in _calculate_reward: {e}")
            return 0.0, None

In [16]:
from imitation.policies.base import FeedForward32Policy, SAC1024Policy, NonTrainablePolicy, RandomPolicy, ZeroPolicy


In [27]:
env = CustomEnv(S=y_test, A=X_test, model=reg, max_step=100, device='cpu')
venv = DummyVecEnv([lambda: env])

# 调整 PPO 参数
# PPO 會梯度消失
model = A2C("MlpPolicy", venv, gamma=0.95,verbose=1, 
            learning_rate=1e-4,  # 降低学习率
            #n_steps=2048,  # 增加每次更新的步数
            #batch_size=64,  # 调整批量大小
            #n_epochs=50,  # 每次更新的 epoch 数
            #gamma=0.99,  # 折扣因子
            #gae_lambda=0.95,  # GAE lambda 参数
            #clip_range=0.2,  # PPO clip 参数
            #ent_coef=0.01,  # 熵系数
            #vf_coef=0.5,  # 价值函数系数
            #max_grad_norm=0.5  # 梯度裁剪
           )

# 增加总时间步
model.learn(total_timesteps=50000)

Using cpu device


ImportError: cannot import name 'maybe_upload_prof_stats_to_manifold' from 'torch._utils_internal' (c:\Users\foresight_User\anaconda3\envs\Python3.9.13\lib\site-packages\torch\_utils_internal.py)

In [5]:
class CustomEnv(gym.Env):
    def __init__(self, S, A, model, max_step=100):
        #self.S = torch.tensor(S, dtype=torch.float32)  # Convert S to torch tensor
        #self.A = torch.tensor(A, dtype=torch.float32)  # Convert A to torch tensor
        
        self.S = S #self._normalize(torch.tensor(S, dtype=torch.float32))#.to(self.device)
        self.A = A #self._normalize(torch.tensor(A, dtype=torch.float32))#.to(self.device)
       
        self.num_samples = int(self.S.shape[0]*0.7)### 0.7 之後當參數
        self.current_step = 0
        self.model = model
        self.max_step = max_step
        self.action_instance = int(self.A.shape[0]*0.7)
        self.action_dim = self.A.shape[1]
        self.action_space = spaces.Box(low=-1e6, high=1e6, shape=(self.num_samples,self.action_dim))
        
        self.obs_dim_S = self.S.shape[1]
     
        self.observation_space = spaces.Box(low=-1e6, high=1e6, shape=(self.num_samples,self.obs_dim_S))
        #print("DONE 1")
        
    # def reset(self):
    #     self.current_step = 0
    #     print("DONE 2")
    #     return self.S.numpy() #self._get_observation()

    def _get_observation(self):
        # self.current_step 放哪?
        num_instance = self.S.shape[0]
        random_index = np.random.randint(0,num_instance, size=int(self.num_samples))
        obs = self.S[random_index,:]#.shape 
        #print("DONE 2")    
        return obs,random_index
    def reset(self):
        self.current_step = 0
        obs , _ = self._get_observation()
        #print("DONE 3")  
        return obs
    def step(self, action):
        next_state, _ = self._get_observation() # _ 為random_index，可能對action有差
        action = torch.tensor(action, dtype=torch.float32)
        #denorm_action = self._denormalize(action, self.A)
        #print("next_state step",next_state.shape)
        #print("action step",action.shape)
        reward,score = self._calculate_reward(action)
        
        best_action = None
        best_score = -np.inf
        if (reward ==1) and (score > best_score):
            best_score = score
            best_action = action #denorm_action #action
            

        done = (self.current_step == self.max_step - 1)
        self.current_step = self.current_step + 1
        #print("DONE 4")  
        return next_state, reward, done, {"best_action":best_action,"best_score":best_score}
    def _calculate_reward(self, action):
        next_state, obs_index = self._get_observation()
        #print("next_state",next_state.shape)
        #print("action ",action.numpy().shape)
        #print("A",self.A.numpy()[obs_index,:].shape)

        #print(action.numpy())
        y_pred_observe = self.model.predict(action.numpy())# action.numpy()
        y_pred = self.model.predict(self.A[obs_index,:]) # self.A 是 NUMPY
        #print(y_pred_observe)
        # y_pred_observe = torch.Tensor(y_pred_observe)
        # y_pred = torch.Tensor(y_pred)
        # denorm_S = self._denormalize(next_state, next_state)
        # denorm_y_pred_observe = self._denormalize(y_pred_observe, next_state)
        # denorm_y_pred = self._denormalize(y_pred, next_state)
        #print(np.isnan(y_pred_observe).any())
        #print(np.isnan(y_pred).any())
        #print(next_state)
        r2_observe = r2_score(next_state, y_pred_observe, multioutput='raw_values') # next_state是 numpy
        r2_ground = r2_score(next_state, y_pred,multioutput='raw_values')
        #print(r2_observe,r2_ground)
        score = None
        if stats.ttest_ind(r2_observe, r2_ground, alternative="greater").pvalue < 0.05:
            reward = float(np.mean(r2_observe) - np.mean(r2_ground)) # 
            score = r2_observe
        elif stats.ttest_ind(r2_observe, r2_ground, alternative="less").pvalue < 0.05:
            reward = float(np.mean(r2_observe) - np.mean(r2_ground))
        else:
            reward = 0.0
        
            return reward, torch.tensor(score).to(self.device) if score is not None else None
        


    # def _normalize(self, tensor):
    #     mean = tensor.mean(dim=0, keepdim=True)
    #     std = tensor.std(dim=0, keepdim=True)

    #     return (tensor - mean) / (std + 1e-8)  # Add small epsilon to avoid division by zero
    
    # def _denormalize(self, tensor, original):
    #     mean = original.mean(dim=0, keepdim=True)
    #     std = original.std(dim=0, keepdim=True)
    #     #print(mean.shape)
    #     #print(std.shape)
    #     return tensor * (std + 1e-8) + mean
    # def step(self, action):
    #     # Apply action and get next state and reward
    #     next_state = self._get_observation()
    #     action = torch.from_numpy(action.astype(np.float64) )
    #     reward = self._calculate_reward(action)
    #     #print("next_state",next_state.shape)
    #     #print("action",action.shape)
    #     #print("reward",reward.shape)
    #     #print("self.current_step",self.current_step)
    #     done = (self.current_step == self.obs_dim_S - 1)
    #     #print("done",done)
    #     self.current_step = self.current_step + 1
    #     #print("self.current_step",self.current_step)
    #     return next_state, reward, done, {}



In [40]:
X_test[0,:].reshape(1,-1)

(1, 53)

In [41]:
env = CustomEnv(S=y[0,:].reshape(1,-1), A=X[0,:].reshape(1,-1), model=reg, max_step=100)
venv = DummyVecEnv([lambda: env])

# 调整 PPO 参数
# PPO 會梯度消失
# 
model = A2C("MlpPolicy", venv, verbose=1, 
            learning_rate=1e-4,  # 降低学习率
            #n_steps=2048,  # 增加每次更新的步数
            #batch_size=64,  # 调整批量大小
            #n_epochs=50,  # 每次更新的 epoch 数
            #gamma=0.99,  # 折扣因子
            #gae_lambda=0.95,  # GAE lambda 参数
            #clip_range=0.2,  # PPO clip 参数
            #ent_coef=0.01,  # 熵系数
            #vf_coef=0.5,  # 价值函数系数
            #max_grad_norm=0.5  # 梯度裁剪
           )

# 增加总时间步
model.learn(total_timesteps=50000)

c:\Users\foresight_User\anaconda3\envs\Python3.9.13\lib\site-packages\stable_baselines3\common\vec_env\patch_gym.py:49: UserWarning: You provided an OpenAI Gym environment. We strongly recommend transitioning to Gymnasium environments. Stable-Baselines3 is automatically wrapping your environments in a compatibility layer, which could potentially cause issues.
  warnings.warn(
c:\Users\foresight_User\anaconda3\envs\Python3.9.13\lib\site-packages\sklearn\metrics\_regression.py:1187: UndefinedMetricWarning: R^2 score is not well-defined with less than two samples.
  warnings.warn(msg, UndefinedMetricWarning)
c:\Users\foresight_User\anaconda3\envs\Python3.9.13\lib\site-packages\sklearn\metrics\_regression.py:1187: UndefinedMetricWarning: R^2 score is not well-defined with less than two samples.
  warnings.warn(msg, UndefinedMetricWarning)
c:\Users\foresight_User\anaconda3\envs\Python3.9.13\lib\site-packages\sklearn\metrics\_regression.py:1187: UndefinedMetricWarning: R^2 score is not well-

Using cpu device


c:\Users\foresight_User\anaconda3\envs\Python3.9.13\lib\site-packages\sklearn\metrics\_regression.py:1187: UndefinedMetricWarning: R^2 score is not well-defined with less than two samples.
  warnings.warn(msg, UndefinedMetricWarning)
c:\Users\foresight_User\anaconda3\envs\Python3.9.13\lib\site-packages\sklearn\metrics\_regression.py:1187: UndefinedMetricWarning: R^2 score is not well-defined with less than two samples.
  warnings.warn(msg, UndefinedMetricWarning)
c:\Users\foresight_User\anaconda3\envs\Python3.9.13\lib\site-packages\sklearn\metrics\_regression.py:1187: UndefinedMetricWarning: R^2 score is not well-defined with less than two samples.
  warnings.warn(msg, UndefinedMetricWarning)
c:\Users\foresight_User\anaconda3\envs\Python3.9.13\lib\site-packages\sklearn\metrics\_regression.py:1187: UndefinedMetricWarning: R^2 score is not well-defined with less than two samples.
  warnings.warn(msg, UndefinedMetricWarning)
c:\Users\foresight_User\anaconda3\envs\Python3.9.13\lib\site-pac

-------------------------------------
| time/                 |           |
|    fps                | 322       |
|    iterations         | 100       |
|    time_elapsed       | 1         |
|    total_timesteps    | 500       |
| train/                |           |
|    entropy_loss       | -75.2     |
|    explained_variance | 0         |
|    learning_rate      | 0.0001    |
|    n_updates          | 99        |
|    policy_loss        | -1.15e-05 |
|    std                | 1         |
|    value_loss         | 2.92e-14  |
-------------------------------------


c:\Users\foresight_User\anaconda3\envs\Python3.9.13\lib\site-packages\sklearn\metrics\_regression.py:1187: UndefinedMetricWarning: R^2 score is not well-defined with less than two samples.
  warnings.warn(msg, UndefinedMetricWarning)
c:\Users\foresight_User\anaconda3\envs\Python3.9.13\lib\site-packages\sklearn\metrics\_regression.py:1187: UndefinedMetricWarning: R^2 score is not well-defined with less than two samples.
  warnings.warn(msg, UndefinedMetricWarning)
c:\Users\foresight_User\anaconda3\envs\Python3.9.13\lib\site-packages\sklearn\metrics\_regression.py:1187: UndefinedMetricWarning: R^2 score is not well-defined with less than two samples.
  warnings.warn(msg, UndefinedMetricWarning)
c:\Users\foresight_User\anaconda3\envs\Python3.9.13\lib\site-packages\sklearn\metrics\_regression.py:1187: UndefinedMetricWarning: R^2 score is not well-defined with less than two samples.
  warnings.warn(msg, UndefinedMetricWarning)
c:\Users\foresight_User\anaconda3\envs\Python3.9.13\lib\site-pac

...

-------------------------------------
| time/                 |           |
|    fps                | 329       |
|    iterations         | 3400      |
|    time_elapsed       | 51        |
|    total_timesteps    | 17000     |
| train/                |           |
|    entropy_loss       | -75.2     |
|    explained_variance | -1.19e-07 |
|    learning_rate      | 0.0001    |
|    n_updates          | 3399      |
|    policy_loss        | 1.09e-05  |
|    std                | 1         |
|    value_loss         | 1.97e-14  |
-------------------------------------


c:\Users\foresight_User\anaconda3\envs\Python3.9.13\lib\site-packages\sklearn\metrics\_regression.py:1187: UndefinedMetricWarning: R^2 score is not well-defined with less than two samples.
  warnings.warn(msg, UndefinedMetricWarning)
c:\Users\foresight_User\anaconda3\envs\Python3.9.13\lib\site-packages\sklearn\metrics\_regression.py:1187: UndefinedMetricWarning: R^2 score is not well-defined with less than two samples.
  warnings.warn(msg, UndefinedMetricWarning)
c:\Users\foresight_User\anaconda3\envs\Python3.9.13\lib\site-packages\sklearn\metrics\_regression.py:1187: UndefinedMetricWarning: R^2 score is not well-defined with less than two samples.
  warnings.warn(msg, UndefinedMetricWarning)
c:\Users\foresight_User\anaconda3\envs\Python3.9.13\lib\site-packages\sklearn\metrics\_regression.py:1187: UndefinedMetricWarning: R^2 score is not well-defined with less than two samples.
  warnings.warn(msg, UndefinedMetricWarning)
c:\Users\foresight_User\anaconda3\envs\Python3.9.13\lib\site-pac

------------------------------------
| time/                 |          |
|    fps                | 328      |
|    iterations         | 3500     |
|    time_elapsed       | 53       |
|    total_timesteps    | 17500    |
| train/                |          |
|    entropy_loss       | -75.2    |
|    explained_variance | 0        |
|    learning_rate      | 0.0001   |
|    n_updates          | 3499     |
|    policy_loss        | 2.11e-05 |
|    std                | 1        |
|    value_loss         | 9.04e-14 |
------------------------------------


c:\Users\foresight_User\anaconda3\envs\Python3.9.13\lib\site-packages\sklearn\metrics\_regression.py:1187: UndefinedMetricWarning: R^2 score is not well-defined with less than two samples.
  warnings.warn(msg, UndefinedMetricWarning)
c:\Users\foresight_User\anaconda3\envs\Python3.9.13\lib\site-packages\sklearn\metrics\_regression.py:1187: UndefinedMetricWarning: R^2 score is not well-defined with less than two samples.
  warnings.warn(msg, UndefinedMetricWarning)
c:\Users\foresight_User\anaconda3\envs\Python3.9.13\lib\site-packages\sklearn\metrics\_regression.py:1187: UndefinedMetricWarning: R^2 score is not well-defined with less than two samples.
  warnings.warn(msg, UndefinedMetricWarning)
c:\Users\foresight_User\anaconda3\envs\Python3.9.13\lib\site-packages\sklearn\metrics\_regression.py:1187: UndefinedMetricWarning: R^2 score is not well-defined with less than two samples.
  warnings.warn(msg, UndefinedMetricWarning)
c:\Users\foresight_User\anaconda3\envs\Python3.9.13\lib\site-pac

KeyboardInterrupt: 

In [4]:
import gym
from gym import spaces
import numpy as np
import torch
from sklearn.metrics import r2_score
from scipy import stats

class CustomEnv(gym.Env):
    def __init__(self, S, A, model, max_step=100, device='cpu'):
        self.device = device
        
        # Normalize S and A
        self.S = torch.tensor(S, dtype=torch.float32)#self._normalize(torch.tensor(S, dtype=torch.float32)).to(self.device)
        self.A = torch.tensor(A, dtype=torch.float32)#self._normalize(torch.tensor(A, dtype=torch.float32)).to(self.device)
        
        self.num_samples = self.S.shape[0]
        self.current_step = 0
        self.model = model
        self.max_step = max_step
        self.action_instance = self.A.shape[0]
        self.action_dim = self.A.shape[1]
        
        # 计算边界（假设数据大致遵循正态分布）
        self.obs_low = float(self.S.min())*1.5
        self.obs_high = float(self.S.max())*1.5
        self.action_low = float(self.A.min())*1.5
        self.action_high = float(self.A.max())*1.5

        # Limit the action space
        self.action_space = spaces.Box(low=self.action_low, high=self.action_high, shape=(self.action_instance, self.action_dim), dtype=np.float32)
        
        self.obs_dim_S = self.S.shape[1]
        self.observation_space = spaces.Box(low=self.obs_low, high=self.obs_high, shape=(self.num_samples, self.obs_dim_S), dtype=np.float32)
        
    # def _normalize(self, tensor):
    #     mean = tensor.mean(dim=0, keepdim=True)
    #     std = tensor.std(dim=0, keepdim=True)
    #     return (tensor - mean) / (std + 1e-8)  # Add small epsilon to avoid division by zero
    
    # def _denormalize(self, tensor, original):
    #     mean = original.mean(dim=0, keepdim=True)
    #     std = original.std(dim=0, keepdim=True)
    #     return tensor * (std + 1e-8) + mean

    def _get_observation(self):
        # self.current_step 放哪?
        num_instance = self.S.shape[0]
        random_index = np.random.randint(0,num_instance, size=int(self.num_samples))
        obs = self.S[random_index,:]#.shape 
        #print("DONE 2")    
        return obs, random_index
    def reset(self):
        self.current_step = 0
        obs , _ = self._get_observation()
        #print("DONE 3")  
        return obs
    
    def step(self, action):
        # 确保动作在边界内
        #action = np.clip(action, -1, 1)
        next_state, index = self._get_observation()
        action = torch.tensor(action, dtype=torch.float32).to(self.device)
        #print(action.shape, self.A.shape)
        # 在使用之前反标准化动作
        denorm_action = action[index,:]#self._denormalize(action, self.A)
        
        reward, score = self._calculate_reward(denorm_action)
        #print("STEP.....","reward: ",reward,"score: ",score)
        best_action = None
        best_score = float('-inf')
        if reward > 0 and score is not None:
            # 如果 score 是张量，取其平均值
            current_score = score.mean().item() if isinstance(score, torch.Tensor) else score
            if current_score > best_score:
                best_score = current_score
                best_action = denorm_action.cpu().numpy()  # 将最佳动作转换为 numpy 数组

        done = (self.current_step == self.max_step - 1)
        self.current_step += 1
        
        return next_state.cpu().numpy(), reward, done, {"best_action": best_action, "best_score": best_score}
    
    def _calculate_reward(self, action):
        try:
            next_state, index = self._get_observation()

            #print(action.shape)
            #print(self.A.shape)
            #print(len(index))
            y_pred_observe = torch.tensor(self.model.predict(action[index,:].cpu().numpy()), dtype=torch.float32).to(self.device)
            y_pred = torch.tensor(self.model.predict(self.A[index,:].cpu().numpy()), dtype=torch.float32).to(self.device)

            # 反标准化预测和真实值以进行正确的 R2 计算
            # denorm_S = self._denormalize(self.S, self.S)
            # denorm_y_pred_observe = self._denormalize(y_pred_observe, self.S)
            # denorm_y_pred = self._denormalize(y_pred, self.S)

            r2_observe = r2_score(next_state.cpu().numpy(), y_pred_observe.cpu().numpy(), multioutput='raw_values')
            r2_ground = r2_score(next_state.cpu().numpy(), y_pred.cpu().numpy(), multioutput='raw_values')

            # 检查 NaN 值
            if np.isnan(r2_observe).any() or np.isnan(r2_ground).any():
                return 0.0, None

            score = None
            #print("r2_observe: ",r2_observe,"r2_ground: ",r2_ground)
            if stats.ttest_ind(r2_observe, r2_ground, alternative="greater").pvalue < 0.05:
                reward = float(np.mean(r2_observe) - np.mean(r2_ground))  # 连续奖励
                score = r2_observe
                
            elif stats.ttest_ind(r2_observe, r2_ground, alternative="less").pvalue < 0.05:
                reward = float(np.mean(r2_observe) - np.mean(r2_ground))  # 负奖励
            else:
                reward = 0.0
            
            return reward, torch.tensor(score).to(self.device) if score is not None else None
        
        except Exception as e:
            print(f"Error in _calculate_reward: {e}")
            return 0.0, None

In [5]:
from sb3_contrib import ARS # 機率輸出不會改變
from stable_baselines3 import A2C # 機率輸出會改變
from stable_baselines3 import DDPG # 輸出機率和動作長依樣?
from stable_baselines3 import HER # 這要搭配其他使用
from stable_baselines3 import PPO # 機率輸出會改變
from stable_baselines3 import SAC # 機率輸出會改變
from stable_baselines3 import TD3 # 輸出機率和動作長依樣?
from sb3_contrib import TRPO
from sb3_contrib import TQC
from sb3_contrib import RecurrentPPO # MlpLstmPolicy

In [7]:
env = CustomEnv(S=y, A=X, model=reg, max_step=100)
venv = DummyVecEnv([lambda: env])

# 调整 PPO 参数
# PPO 會梯度消失
# DDPG SAC 記憶體用量太大
# 
model = A2C("MlpPolicy", venv, verbose=1, 
            learning_rate=1e-4,  # 降低学习率
            n_steps=128,  # 增加每次更新的步数
            #batch_size=64,  # 调整批量大小
            #n_epochs=50,  # 每次更新的 epoch 数
            gamma=0.95,  # 折扣因子
            gae_lambda=0.95,  # GAE lambda 参数
            #clip_range=0.2,  # PPO clip 参数
            ent_coef=0.01,  # 熵系数
            vf_coef=0.5,  # 价值函数系数
            max_grad_norm=0.5  # 梯度裁剪
           )

# 增加总时间步
model.learn(total_timesteps=50000)

c:\Users\foresight_User\anaconda3\envs\Python3.9.13\lib\site-packages\stable_baselines3\common\vec_env\patch_gym.py:49: UserWarning: You provided an OpenAI Gym environment. We strongly recommend transitioning to Gymnasium environments. Stable-Baselines3 is automatically wrapping your environments in a compatibility layer, which could potentially cause issues.
  warnings.warn(


Using cpu device
-------------------------------------
| time/                 |           |
|    fps                | 8         |
|    iterations         | 100       |
|    time_elapsed       | 1548      |
|    total_timesteps    | 12800     |
| train/                |           |
|    entropy_loss       | -3.76e+05 |
|    explained_variance | -0.0658   |
|    learning_rate      | 0.0001    |
|    n_updates          | 99        |
|    policy_loss        | -4.16e+06 |
|    std                | 1         |
|    value_loss         | 131       |
-------------------------------------
-------------------------------------
| time/                 |           |
|    fps                | 8         |
|    iterations         | 200       |
|    time_elapsed       | 3097      |
|    total_timesteps    | 25600     |
| train/                |           |
|    entropy_loss       | -3.76e+05 |
|    explained_variance | -0.0394   |
|    learning_rate      | 0.0001    |
|    n_updates          | 199    

In [11]:
y_pred = reg.predict(model.predict(y)[0])
from sklearn.metrics import r2_score
r2_score(y, y_pred,multioutput='raw_values')

array([-0.39047988, -0.37953505, -0.41378321, -0.41556336, -0.38813482,
       -0.41366773, -0.44592131, -0.45035988, -0.41088014, -0.42414662,
       -0.4319457 , -0.42258383, -0.42343244, -0.39757575, -0.43525734,
       -0.4254717 , -0.41743848, -0.40745299, -0.42558758, -0.41488008,
       -0.40284971, -0.37823484, -0.40060906, -0.4081078 , -0.39994977,
       -0.37863568, -0.42086831])